## clustering attempt

In [1]:
import re
import json
import pandas as pd
import numpy as np
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from sentence_transformers import SentenceTransformer
from sklearn.cluster import DBSCAN
from transformers import pipeline


In [5]:
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('punkt_tab')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\jared\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\jared\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\jared\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\jared\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [7]:
pd.set_option('display.max_colwidth', None)

Process:

1) want list of each article's title + description
2) clean data (lowercase, remove html, remove special chars)
3) preprocess (tokenize and remove stopwords, lemmatize)
4) use kmeans for clustering (q: fixed number of clusters?)
5) apply PCA
6) select only largest clusters?
7) web scrape articles belonging to that cluster
8) summarize with OpenAI

In [4]:
# Step 1: read in data
def read_data(file_path):
    with open(file_path) as f:
        data = json.load(f)
    return data

search_data = read_data('../newsapi/outputs/test_search_trump.json')

In [5]:
# Step 1 cont: convert to DF
articles_df = pd.json_normalize(search_data)


In [7]:
# Step 2: clean and tokenize data
def clean_text(text):
    if not isinstance(text, str):
        return ""
    text = text.lower()
    text = re.sub(r'http\S+|www\S+|https\S+', '', text)
    text = re.sub(r'\W+', ' ', text)
    tokens = word_tokenize(text)
    tokens = [word for word in tokens if word not in stopwords.words('english')]
    lemmatizer = WordNetLemmatizer()
    tokens = [lemmatizer.lemmatize(word) for word in tokens]
    return ' '.join(tokens)

articles_df['combined_text'] = articles_df['title'].fillna('') + ' ' + articles_df['description'].fillna('')
articles_df['processed_text'] = articles_df['combined_text'].apply(clean_text)

In [8]:
# Step 3: embed and cluster using DBSCAN (can also try kmeans)
model = SentenceTransformer('all-MiniLM-L6-v2')
embeddings = model.encode(articles_df['processed_text'].fillna(''))

dbscan = DBSCAN(eps=0.5, min_samples=3, metric='cosine')
clusters = dbscan.fit_predict(embeddings)

articles_df['cluster'] = clusters

In [16]:
articles_df['cluster'].value_counts()

cluster
-1    87
 0    13
 2     9
 5     6
 1     4
 4     4
 6     3
 3     3
Name: count, dtype: int64

In [17]:
print(articles_df[articles_df['cluster'] == 0]['title'])
print(articles_df[articles_df['cluster'] == 0]['description'])

0                                          What Donald Trump's Win Will Mean for Big Tech
3               More Spyware, Fewer Rules: What Trump’s Return Means for US Cybersecurity
46                           How will a second Trump presidency affect the tech industry?
51               Did you need another reminder that Donald Trump watches TV? Here you go.
59     Elon Musk went all-in on Pennsylvania — and his expensive effort paid off big time
68           Silicon Valley is betting a Musk-inspired Trump could unleash a startup boom
102                                       What Donald Trump’s Win Could Mean for Vaccines
103                             How long will Elon Musk and Donald Trump’s lovefest last?
105                                           What Donald Trump’s Win Means For Inflation
108                                    What Trump's win means for the consulting industry
109                                                  What Trump’s Win Means for Education
119       

In [24]:
# step 4: summarize main clusters (may use OpenAI for this in the future)
summaries = []
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
for cluster in articles_df['cluster'].unique():
    if cluster == -1:
        continue
    cluster_articles = articles_df[articles_df['cluster'] == cluster]['combined_text']
    combined_text = ' '.join(cluster_articles[:15])
    if combined_text.strip():
        summary = summarizer(combined_text, max_length=50, min_length=30, do_sample=False)
        summaries.append({'cluster': cluster, 'summary_text': summary[0]['summary_text']})
        print(f"Cluster {cluster} Summary: {summary[0]['summary_text']}")

Cluster 0 Summary:  Trump's approach to Big Tech has oscillated between calls for stricter regulations for some players and a hands-off approach for others . Silicon Valley is betting a Musk-inspired Trump could unleash a startup boom . The president-elect returned to
Cluster 1 Summary:  Jeff Bezos says he’s a climate guy — why is he kissing the ring? Jeff Bezos joined other tech moguls in congratulating Trump on his election victory . COP29 climate summit opens amid fears the US election will derail efforts
Cluster 2 Summary:  Pete Hegseth, a Fox News host, has advocated for a conservative cultural shift in the US military . On a podcast last week, he said he didn't want US intervention forcing Putin's hand . With Trump's White House
Cluster 5 Summary:  Arizona was that last state to be called by the Associated Press in the presidential race . It brings Trump's total electoral vote count to 312, with 226 for Vice President Harris .
Cluster 6 Summary:  Trump fans and Harris supporters 

In [ ]:
# PSA I tried it with OpenAI and summaries are much better. So we'll probably use that.

In [2]:
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

pd.set_option('display.max_colwidth', None)

model = SentenceTransformer('all-MiniLM-L6-v2')
dbscan = DBSCAN(eps=0.5, min_samples=3, metric='cosine')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\jared\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\jared\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\jared\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [3]:
def clean_text(text):
    if not isinstance(text, str):
        return ""
    text = text.lower()
    text = re.sub(r'http\S+|www\S+|https\S+', '', text)
    text = re.sub(r'\W+', ' ', text)
    tokens = word_tokenize(text)
    tokens = [word for word in tokens if word not in stopwords.words('english')]
    lemmatizer = WordNetLemmatizer()
    tokens = [lemmatizer.lemmatize(word) for word in tokens]
    return ' '.join(tokens)

dbscan2 = DBSCAN(eps=0.2, min_samples=5, metric='cosine')

def cluster_daily_news(filename):
    with open(filename, 'r', encoding='utf-8') as f:
        articles_data = json.load(f)
    articles_df = pd.json_normalize(articles_data)
    articles_df['combined_text'] = articles_df['title'].fillna('') + ' ' + articles_df['content'].fillna('')
    articles_df['processed_text'] = articles_df['combined_text'].apply(clean_text)
    embeddings = model.encode(articles_df['processed_text'].fillna(''))
    clusters = dbscan.fit_predict(embeddings)
    articles_df['cluster'] = clusters
    id_to_cluster = dict(zip(articles_df.index, articles_df['cluster']))
    return id_to_cluster

def extract_first_sentence(text):
    if not isinstance(text, str) or text.strip() == "":
        return ""
    sentences = nltk.sent_tokenize(text)
    return sentences[0] if sentences else ""

def cluster_daily_news_titles(filename):
    with open(filename, 'r', encoding='utf-8') as f:
        articles_data = json.load(f)
    articles_df = pd.json_normalize(articles_data)
    articles_df['first_sentence'] = articles_df['content'].fillna('').apply(extract_first_sentence)
    articles_df['combined_text'] = articles_df['title'].fillna('') + " " + articles_df['first_sentence'].fillna('')
    articles_df['processed_text'] = articles_df['combined_text'].apply(clean_text)
    embeddings = model.encode(articles_df['processed_text'].fillna(''))
    clusters = dbscan2.fit_predict(embeddings)
    articles_df['cluster'] = clusters
    id_to_cluster = dict(zip(articles_df.index, articles_df['cluster']))
    return id_to_cluster

In [4]:
path = r"C:\Users\jared\OneDrive\Desktop\bitewise\python-api\data\articles_data.json"


In [7]:
cluster_dict = cluster_daily_news(path)
print(set(cluster_dict.values()))

{0, 1, 2, 3, -1}


In [5]:
cluster_dict_titles = cluster_daily_news_titles(path)
print(set(cluster_dict_titles.values()))

{0, 1, 2, 3, 4, -1}


In [34]:
def remove_articles_by_source(input_file, output_file, source_to_remove):
    # Read the JSON data
    with open(input_file, 'r', encoding='utf-8') as f:
        articles_data = json.load(f)
    
    # Filter out articles with the specified source
    filtered_articles = [
        article for article in articles_data if article.get('source') != source_to_remove
    ]
    
    # Save the cleaned data back to a new file (or overwrite the original file)
    with open(output_file, 'w', encoding='utf-8') as f:
        json.dump(filtered_articles, f, indent=4, ensure_ascii=False)
    
    print(f"Removed articles from source: {source_to_remove}")
    print(f"Remaining articles: {len(filtered_articles)}")

path = r"C:\Users\jared\OneDrive\Desktop\bitewise\python-api\data\articles_data.json"
source_to_remove = 'https://www.businessinsider.com/'
remove_articles_by_source(path, path, source_to_remove)


Removed articles from source: https://www.businessinsider.com/
Remaining articles: 1264


In [13]:
# path = r"C:\Users\jared\OneDrive\Desktop\bitewise\python-api\data\articles_data.json"
from features import get_source_and_bias, estimate_reading_time, char_length

# add cluster label to articles
with open(path, 'r', encoding='utf-8') as f:
    articles_data = json.load(f)
articles_df = pd.DataFrame(articles_data)
articles_df['cluster'] = articles_df.index.map(cluster_dict_titles)

def process_article(article):
    article['source'], article['biasRating'] = get_source_and_bias(article.get('source', {}))
    article['readTime'] = estimate_reading_time(char_length(article.get('content', None)))
    return article

articles_df = articles_df.apply(lambda x: process_article(x), axis=1)

# get top clusters
top_clusters = (
    articles_df['cluster']
    .value_counts()
    .nlargest(4)
    .index
)

# get articles for top clusters
top_articles = articles_df[articles_df['cluster'].isin(top_clusters)]

response = (
    top_articles
    .groupby('cluster')
    .apply(lambda x: x.to_dict(orient='records'))
    .to_dict()
)


{-1: [{'url': 'https://games.mashable.com/games/daily-crossword', 'title': 'Play Now: Daily Crossword', 'source': 'Mashable', 'content': "Advertisement Player support Advertisement Daily Crossword players also enjoy: The best free online crossword is brand newevery day. No pencil or eraser required! Each new puzzle offers a refreshing challenge, with clues ranging from easy to tricky, ensuring there's something for everyone. Solve across and down clues, using your word skills and general knowledge to fill in the grid. Plus, with no cleanup needed, you can keep your mind engaged without the hassle of paper and pencil. Tune in every day for a new puzzle to solve and a fresh challenge! Instantly play your favorite free online games including card games, puzzles, brain games & dozens of others, brought to you by Mashable.", 'cluster': -1, 'biasRating': 'left', 'readTime': '<2 min'}, {'url': 'https://fortune.com/author/associated-press/', 'title': 'The Associated Press', 'source': 'Fortune'

C:\Users\jared\AppData\Local\Temp\ipykernel_29300\831411430.py:31: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(lambda x: x.to_dict(orient='records'))


In [3]:
import os
from features import get_source_and_bias, estimate_reading_time, char_length
json_file_path = r'C:\Users\jared\OneDrive\Desktop\bitewise\python-api\data\articles_data.json'

# apply clustering and get top 4 clusters
cluster_dict = cluster_daily_news_titles(json_file_path)
print(set(cluster_dict.values()))

# add cluster label to articles
with open(json_file_path, 'r', encoding='utf-8') as f:
    articles_data = json.load(f)
articles_df = pd.DataFrame(articles_data)
articles_df['cluster'] = articles_df.index.map(cluster_dict)

def process_article(article):
    article['source'], article['biasRating'] = get_source_and_bias(article.get('source', {}))
    article['readTime'] = estimate_reading_time(char_length(article.get('content', None)))
    return article

articles_df['processed_article'] = articles_df.apply(lambda x: process_article(x.to_dict()), axis=1)

# get top clusters
top_clusters = (
    articles_df['cluster']
    .value_counts()
    .nlargest(4)
    .index
)

# get articles for top clusters
top_articles = articles_df[articles_df['cluster'].isin(top_clusters)]
response = (
    top_articles['processed_article']
    .groupby('cluster')
    .apply(lambda x: x.to_dict(orient='records'))
    .to_dict()
)
print(response)

NameError: name 'cluster_daily_news_titles' is not defined

In [22]:
top_articles

url  \
3                                           https://mashable.com//article/notre-dame-ohio-state-college-football-2025-live-stream   
4                                                                  https://mashable.com//article/strands-nyt-hint-january-20-2025   
5                                                             https://mashable.com//article/melania-trump-hat-inauguration-outfit   
6                                                              https://fortune.com/2025/01/20/donald-trump-inauguration-speech-2/   
12                                                                 https://mashable.com//article/trump-executive-order-tiktok-ban   
...                                                                                                                           ...   
1310                                                      https://www.vogue.com//article/what-people-are-wearing-pre-inauguration   
1313      https://www.pbs.org/newshour/show/why-netanyahu-announced-a-last-minute-snag-in-israel-hamas-ceasefire-and-hostage-deal   
1316               https://www.esquire.com/news-politics//news-politics/politics/a60787873/republican-senators-visit-trump-trial/   
1318  https://www.salon.com//2025/01/20/biden-issues-clemency-to-family-democratic-politicians-and-leonard-peltier/?in_brief=true   
1320             https://www.esquire.com/news-politics//news-politics/politics/a63373441/trump-legal-battle-panama-hotel-project/   

                                                                                            title  \
3                                                   How to watch Notre Dame vs. Ohio State online   
4                                                       NYT Strands hints, answers for January 20   
5                           Melania Trump's inauguration hat draws comparisons to Carmen Sandiego   
6     Trump returns to power promising retribution, reversal of the Biden era, and a trip to Mars   
12                                                          Back like it never leftTikTok is back   
...                                                                                           ...   
1310                            The Most Notable Fashion Moments From the Pre-Inauguration Events   
1313        Why Netanyahu announced a last-minute snag in Israel-Hamas ceasefire and hostage deal   
1316                                                     Aww, Trump Brought Some Buddies to Court   
1318                                  Jan 20, 1:40 pm ESTBiden grants clemency to Leonard Peltier   
1320                                           Gee, I Wonder Why Trump Is So Interested in Panama   

                                      source  \
3                      https://mashable.com/   
4                      https://mashable.com/   
5                      https://mashable.com/   
6                       https://fortune.com/   
12                     https://mashable.com/   
...                                      ...   
1310                  https://www.vogue.com/   
1313           https://www.pbs.org/newshour/   
1316  https://www.esquire.com/news-politics/   
1318                  https://www.salon.com/   
1320  https://www.esquire.com/news-politics/   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   